In [211]:
import pandas as pd
import numpy as np
import os
#import gensim
#from nltk import ngrams
from tqdm import tqdm

In [2]:
from keras.models import Sequential
from keras.layers import Dense, LSTM, GRU, Embedding, Dropout, Activation, Flatten,Conv1D, MaxPooling1D
from keras.utils import to_categorical
from keras.preprocessing.sequence import pad_sequences
from keras.preprocessing.text import Tokenizer

Using TensorFlow backend.


In [3]:
train = pd.read_csv('train.csv')
test = pd.read_csv('test.csv')
submission = pd.read_csv('sample_submission.csv')

In [4]:
f_train = train.groupby('UID').Event_Code.apply(lambda x: " ".join(x)).reset_index()

In [5]:
seq_tran = f_train.Event_Code.apply(lambda x: x.split())

In [19]:
tokenizer = Tokenizer()
tokenizer.fit_on_texts(seq_tran)

In [20]:
encoder = tokenizer.texts_to_sequences(seq_tran)
vocab_size = len(tokenizer.word_index)
print(vocab_size)

6472


In [21]:
sequences = list()
length = list()
for ii in encoder:
    length.append(len(ii))
    for iq in range(5,len(ii)):
        sequence = ii[iq-5:iq+1]
        sequences.append(sequence)

In [22]:
max_len_sq = max([len(seq) for seq in sequences])
max_len_sq

6

In [23]:
sequences = pad_sequences(sequences,maxlen=max_len_sq,padding="pre")

In [24]:
sequences = np.array(sequences)

In [25]:
X,y = sequences[:,:-1],sequences[:,-1]

In [26]:
X.shape,y.shape

((751787, 5), (751787,))

In [53]:
X=np.concatenate((X,X),axis=0)
y=np.concatenate((y,y))

In [27]:
embedding_size = 500

In [58]:
model = Sequential()
model.add(Embedding(vocab_size,embedding_size,input_length=5))
model.add(GRU(embedding_size))
#model.add(Dropout(0.3))
model.add(Dense(units=vocab_size, activation="softmax"))
model.compile(optimizer="RMSprop",loss="sparse_categorical_crossentropy")

In [55]:
model.summary()

_________________________________________________________________
Layer (type)                 Output Shape              Param #   
embedding_11 (Embedding)     (None, 5, 500)            3236000   
_________________________________________________________________
gru_11 (GRU)                 (None, 500)               1501500   
_________________________________________________________________
dropout_8 (Dropout)          (None, 500)               0         
_________________________________________________________________
dense_11 (Dense)             (None, 6472)              3242472   
Total params: 7,979,972
Trainable params: 7,979,972
Non-trainable params: 0
_________________________________________________________________


In [57]:
#model.fit(X,y,epochs=20,batch_size=256,verbose=1,validation_split=0.1)

In [ ]:
import pickle
pickle.dump(model.to_json(),open('rnn_gru_500_20_512_full_v2.keras','wb'))

In [71]:
import h5py
import keras

In [ ]:
model.save_weights('rnn_gru_500_20_512_full_v2.weights')

In [59]:
model.load_weights('rnn_gru_500_20_512_v1.weights')

In [162]:
f_train['last_five']= f_train.Event_Code.apply(lambda x: ' '.join(x.split()[-5:]))

In [163]:
final_test = pd.merge(f_train[['UID','last_five']],test[['UID']],on="UID",how="left")

In [205]:
f_test_seq = final_test['last_five']
final_test.head()

UID                 last_five
0  Id_e45a3682  7334 2214 3258 8005 7087
1  Id_e45a3683  8502 2773 2773 9921 3489
2  Id_e45a3684  4011 9636 7855 3264 2533
3  Id_e45a3685  3209 5621 2627 2533 V761
4  Id_e45a3686  3194 9921 3194 8004 7140

In [215]:
def get_output(model,tokenizer,max_length,seed_data,n_data):
    in_seq = seed_data
    
    #print('Initial In_seq:>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>>',in_seq)
    
    for _ in range(10):
        enc = tokenizer.texts_to_sequences([in_seq])
        enc = pad_sequences(enc,maxlen=max_length,padding="pre")
        #print('padding data:>>>>>>>>>>',enc)
        output = model.predict_classes(enc,verbose=0)
        out_seq = ""
        for event, index in tokenizer.word_index.items():
            if index == output:
                out_seq = event
                break
        #print('Out_event:>>>>>>>',event)
        in_seq += " "+ event
        #print('Next in_seq is:>>>>>>>>>>>>>>>>>>>>>>',in_seq)
        '''
    for _ in range(n_data):
        #encod = tokenizer.texts_to_sequences(in_seq)[0]
        #encod = pad_sequences(in_seq,maxlen=max_length,padding="pre")
        output = model.predict_classes(np.array(in_seq),verbose=0)
        out_seq.append(output)
        
        out_event = ''
        for event, index in tokenizer.word_index.items():
            if index == output:
                out_event = event
                break
        out_seq.append(out_event)
        
        in_s
      '''
    return in_seq.split()[-10:] 

In [212]:
tqdm.pandas()

In [229]:
final_test['final_10'] = final_test.last_five.progress_apply(lambda x: get_output(model,tokenizer,5,x,10))


  5%|▌         | 162/3000 [00:36<08:56,  5.29it/s]


 11%|█         | 322/3000 [01:11<08:49,  5.06it/s]


 16%|█▌        | 482/3000 [01:46<09:53,  4.24it/s]


 21%|██▏       | 642/3000 [02:22<08:34,  4.59it/s]


 27%|██▋       | 802/3000 [02:58<08:54,  4.11it/s]


...

 79%|███████▉  | 2376/3000 [08:47<02:10,  4.77it/s]


 84%|████████▍ | 2533/3000 [09:21<01:33,  4.98it/s]


 90%|████████▉ | 2690/3000 [09:55<01:09,  4.48it/s]


 95%|█████████▍| 2847/3000 [10:30<00:33,  4.61it/s]


100%|██████████| 3000/3000 [11:04<00:00,  4.47it/s]


In [227]:
final = pd.DataFrame(final_test.final_10.values.items(), columns=list(submission)[1:], index=final_test.UID)

AttributeError: 'numpy.ndarray' object has no attribute 'items'

In [233]:
final_test[["UID","final_10"]].to_csv('submi_1112.csv',index=False)

In [230]:
type(final_test.final_10)

pandas.core.series.Series

In [224]:
final_test[list(submission)[1:]]= 

['Event1',
 'Event2',
 'Event3',
 'Event4',
 'Event5',
 'Event6',
 'Event7',
 'Event8',
 'Event9',
 'Event10']

In [306]:
seq_seq = list(seq_tran.apply(lambda x: [y for y in x]))
seq_seq

[['2214',
  '2214',
  '4939',
  '3258',
  '4848',
  '2214',
  '3641',
  '2214',
  '2214',
  '2214',
  '2214',
  '8561',
  '3258',
  '3258',
  '7151',
  '2214',
  '8256',
  '3106',
  '2214',
  '2214',
  '3051',
  '2214',
  '7087',
  '7087',
  'V252',
  '7087',
  '2214',
  'V728',
  '8501',
  '2270',
  '2214',
  '7087',
  '7087',
  '3641',
  '2214',
  '3180',
  '9300',
  '2214',
  '2214',
  '7102',
  '2214',
  '8690',
  '7087',
  '8561',
  '7087',
  '7087',
  '4032',
  '2214',
  '3258',
  '7931',
  '8690',
  'V588',
  '3258',
  '7087',
  '7153',
  '3258',
  '7087',
  '9201',
  '3258',
  '8561',
  '7087',
  '2214',
  '8501',
  '2214',
  '7087',
  '3674',
  'V728',
  '4939',
  '2214',
  '2214',
  '2214',
  'V586',
  '3180',
  '7087',
  '1210',
  '8501',
  '7087',
  '7087',
  '2214',
  '3258',
  '2214',
  '3258',
  '7087',
  '2214',
  '3258',
  '3258',
  '2214',
  '3258',
  '7087',
  '3180',
  '2729',
  '8452',
  '7087',
  '3258',
  '2214',
  '7087',
  '3180',
  '3258',
  '2214',
  '7087',


In [16]:
sequ = list()
for ii in seq_seq:
    for iq in range(2,len(seq_seq)):
        sequence = seq_seq[iq-2:iq+1]
        sequ.append(sequence)

NameError: name 'seq_seq' is not defined

In [308]:
print("total sequence is :",len(sequ))

total sequence is : 8994000


In [310]:
sequ = pad_sequences(sequ,maxlen=3,padding="pre")

ValueError: setting an array element with a sequence.

In [ ]:
sequ

In [294]:
embedding_model = gensim.models.Word2Vec(seq_seq,min_count=0,workers=3,sg=0,max_vocab_size=300,iter=100,hs=1,window=5)

In [281]:
fastext_model = gensim.models.FastText(seq_seq,min_count=0,sg=1,workers=3,max_vocab_size=300,iter=100)

In [282]:
embedding_model.save("embedding.w2v")
fastext_model.save('embedding.fastext')

In [284]:
word2idx = {}

In [285]:
for i in embedding_model.wv.vocab:
    if i not in word2idx:
        word2idx[i] = embedding_model.wv.vocab[i].index

In [298]:
embedding_model.wv.vector_size

100

In [270]:
train_x, train_y = sequences[:,:4],sequences[:,-1]

In [271]:
train_x.shape,train_y.shape

((766787, 4), (766787,))

In [263]:
for i in ngrams(seq_list_data[0][:5],n=5,pad_left=True,left_pad_symbol=6473):
    print(list(i))

[6473, 6473, 6473, 6473, 604]
[6473, 6473, 6473, 604, 604]
[6473, 6473, 604, 604, 31]
[6473, 604, 604, 31, 1433]
[604, 604, 31, 1433, 143]


In [6]:
seq_id = np.array(seq_tran)

In [87]:
def word2idx(evnt_code):
    return emb.wv.vocab[evnt_code].index

def idx2word(evnt_code):
    return emb.wv.index2word[evnt_code]

In [191]:
X,Y = train_x[4432],train_y[4432]

In [303]:
type(encoder)

list

In [228]:
sequences = []

In [229]:
for ii in seq_list_data:
    for iq in range(5,len(ii)):
        sequence = ii[iq-5:iq+1]
        sequences.append(sequence)

In [230]:
max_len_sq = max(len(seq) for seq in sequences)
max_len_sq

6

In [231]:
sequences = np.array(sequences)

In [232]:
train_x = sequences[:,:5]
train_y = sequences[:,-1]
train_x.shape, train_y.shape

((751787, 5), (751787,))

In [138]:
x_train = np.concatenate((train_x,train_x,train_x))
y_train = np.concatenate((sequences[:,-3],sequences[:,-2],sequences[:,-1]))

In [140]:
x_train.shape,y_train.shape

((2228361, 5), (2228361,))

In [233]:
pretrained_weights = emb.wv.vectors

In [234]:
vocab_size, embedding_size = pretrained_weights.shape

In [235]:
vocab_size, embedding_size

(6472, 300)

In [179]:
model = Sequential()
model.add(Embedding(vocab_size,embedding_size,weights=[pretrained_weights],trainable=False,input_length=10))
model.add(GRU(embedding_size))
model.add(Dropout(0.3))
model.add(Dense(units=vocab_size, activation="softmax"))
model.compile(optimizer="adam",loss="sparse_categorical_crossentropy")

In [186]:
train_x[4432],train_y[4432]

(array([   2,  355,  538,  147,    4, 2167,  231,  341,  103,  485]), 40)

In [187]:
model.predict_classes(x=np.array([train_x[4432]]))

array([0], dtype=int64)

In [60]:
def get_next10(data):
    

array([605], dtype=int64)

In [61]:
y[0]

144